## Step 1 & 2: Create 'thalassaDB' to Explore and Generate New Data from Our Database.<br><br> That was solved in 'sql_Queries' file.

####

## Step 3: Specific EDA 

In [ ]:
import numpy as np
import pandas as pd
from datetime import datetime
import geopandas as gpd
import warnings
import folium
import matplotlib.pyplot as plt
warnings.filterwarnings("ignore")

__We load data from a CSV files contained within the 'thalassaDB' PostgreSQL database and load them into Pandas and GeoPandas DataFrames.__

In [2]:
gdf_ports = gpd.read_file('../Dataset_after/ports_new.csv')
gdf_positions = gpd.read_file('../Dataset_after/positions_new.csv')
vessels_df = pd.read_csv('../Dataset_after/vessels_new.csv')
vesselstypes_df = pd.read_csv('../Dataset_after/vesselstypes_new.csv')

In [3]:
len(gdf_ports), len(gdf_positions), len(vessels_df), len(vesselstypes_df)

(26, 7036651, 489, 106)

__The Positions table have information about the positions and characteristics of vessels at specific timestamps.__

In [4]:
gdf_positions.head()

id                                          vessel_id  \
0  4759345  db8d405a51544e40c15f6d136ce9f43a066348515cf1c7...   
1  4759346  6bc223ad679d485bbb5f7755946fc7b9fd5ad61ef130fa...   
2  4759348  bfca0e846b6d35f8fde7611da7ff55835ba71a7eda53d3...   
3  4759349  1306b54640da6db29305db9ff22f30d5eef14fc5a72f44...   
4  4759350  4008373ec23cf3e89faa9534e929a2c52170d0c7b8e19e...   

                     t       lon       lat heading course speed  \
0  2019-08-12 13:50:09  23.54886  37.82956     270  262.9   7.8   
1  2019-08-12 13:50:10  23.60567    37.959     313            0   
2  2019-08-12 13:50:11  23.64103  37.94484     211    0.1     0   
3  2019-08-12 13:50:11  23.64798   37.9326          298.1     0   
4  2019-08-12 13:50:11  23.60677  37.94933          279.4     0   

                                   location_geometry  distance_in_meters  \
0  0101000020E61000002315C616828C3740EE08A7052FEA...  15353.902301266455   
1  0101000020E6100000172B6A300D9B3740986E1283C0FA...   4021.820727356439   
2  0101000020E610000040C1C58A1AA43740F0F96184F0F8...   558.6382617338202   
3  0101000020E61000004B766C04E2A53740F31FD26F5FF7...  1252.0862365424923   
4  0101000020E6100000A5315A47559B37404C8E3BA583F9...   3609.530917103893   

  geometry  
0     None  
1     None  
2     None  
3     None  
4     None

__The Ports table have information about ports, including their names and geographic coordinates.__

In [5]:
gdf_ports.head()

name                 lon       lat geometry_polygon  \
0      ZEA  23.648989999999998  37.93486                    
1  SOUSAKI            23.05575   37.9168                    
2     SIRI            24.06864  37.74283                    
3   RAFINA            24.01164  38.02345                    
4   PERAMA  23.567320000000002  37.96085                    

                                      geometry_point geometry  
0  0101000020E6100000586E693524A63740562B137EA9F7...     None  
1  0101000020E610000083C0CAA1450E3740857CD0B359F5...     None  
2  0101000020E61000008B321B64921138406C3EAE0D15DF...     None  
3  0101000020E61000005053CBD6FA023840AC8BDB680003...     None  
4  0101000020E6100000E25D2EE23B913740492EFF21FDFA...     None

__The Vessels table have information about each vessel in the dataset.__

In [6]:
vessels_df.head()

id  type    flag  \
0  05689045c30e372c6603b3db8312f9d7444c75b42ff879...  37.0  Cyprus   
1  b6ce45e37aff96757b2a87fd26dc99a7ec304823216468...  40.0  Cyprus   
2  5b53cea1893df61389767637884d1188ca8a9da7ebce5b...  70.0  Cyprus   
3  77a52ea9efafd351d2d027808b516c1dbf5acf95c3e246...  84.0  Cyprus   
4  04b6c84a518f833b7206a114ada7660d56888de1af6cab...  70.0  Cyprus   

                                 type_description  
0                                  Pleasure Craft  
1  High speed craft (HSC), all ships of this type  
2                   Cargo, all ships of this type  
3                    Tanker, Hazardous category D  
4                   Cargo, all ships of this type

__The VesselTypes table provides descriptions for various vessel types.__

In [7]:
vesselstypes_df.head()

code              description
0     0  Not available (default)
1     1  Reserved for future use
2     2  Reserved for future use
3     3  Reserved for future use
4     4  Reserved for future use

####

### **Task 1:** For a specific passenger ship (which we will choose from the Vessels table) and a specific day (let's say August 16, 2019) for which we have previously confirmed that the ship has provided waypoints, how many waypoints have been recorded? What are the minimum, average, and maximum time intervals between two consecutive waypoints?

In [8]:
gdf_positions.t.is_monotonic_increasing

False

In [9]:
# Short the gdf_positions in ascending order based on time
gdf_positions.sort_values(by='t', inplace=True)
gdf_positions.t.is_monotonic_increasing

True

In [10]:
# Convert t column to datetime
gdf_positions.t = pd.to_datetime(gdf_positions['t'])

We initiate the process by identifying passenger vessels using vessel type codes within the range of 60 to 69. Subsequently, we compile a list of distinct passenger vessel IDs

In [11]:
passenger_vessels = []
for i in range(len(vessels_df)):
    vessel_type = vessels_df['type'].iloc[i]
    if not pd.isna(vessel_type) and 60 <= int(vessel_type) <= 69:
        passenger_vessels.append(vessels_df['id'].iloc[i])

print('We have', len(np.unique(passenger_vessels)), 'unique passenger vessels in table Vessels\n')

We have 64 unique passenger vessels in table Vessels



Next, we determine which of these passenger vessels have records dated August 16, 2019.

In [12]:
# Filter 'gdf_positions' DataFrame to get positions recorded on August 16, 2019
positions_2019_08_16 = gdf_positions[gdf_positions['t'].dt.date == pd.to_datetime('2019-08-16').date()]

# Filter positions for passenger vessels based on their 'vessel_id'
passenger_vessels_in_positions = positions_2019_08_16[positions_2019_08_16['vessel_id'].isin(passenger_vessels)]

# Get unique passenger vessel IDs from the filtered positions
unique_passenger_vessels_in_positions = passenger_vessels_in_positions['vessel_id'].unique()

print('We have', len(unique_passenger_vessels_in_positions), 'unique passenger vessels in positions on August 16, 2019, which\n')
print('The first 10 unique passenger vessels in positions on August 16, 2019, are:\n', unique_passenger_vessels_in_positions[:10])

We have 40 unique passenger vessels in positions on August 16, 2019, which

The first 10 unique passenger vessels in positions on August 16, 2019, are:
 ['7f080c68ffb5cbe042d98b2524fc8a56db5bb75315f1063e6fa7440d20881f8e'
 '5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b16077c9c38969fb2de'
 '17a2772f901d45b69647ab7ed764ba82c5028da1c59480bda6eca2bce640c27c'
 '41c938019e2983d8538804723b79d67a2c853ed9a027e75e1ea916d36b277a74'
 '98bb01857390ca864cb823439f8a5f32bdb38ff27ccab30a0c930d9f2ef15273'
 '8be4c17e6c22819d92843b1a5bc575e9f91932f8da33a3cdec145eebfbe9dd63'
 '2aeba00a7deef3d7c5af0df1b314a63d9e3e7d9b164cc0133fc9966d52b0ba2f'
 'baf28036cf604ca60971481a836408196e1abf077c7b9dc04d0221cdcb41369e'
 'f6bc7f1c524e9ddb5ebee6ea1012f54502556638891b604dcd17ee19cf4e2b4f'
 'e21ce5e3044c8884528db8e831bd2cb62e834d51d204868183f06a6971dbb3b9']


Now we know for sure the 40 vessel IDs that had records on August 16, 2019. We chose the 2nd vessel ID of the printed list.<br>
As we selected the vessel ID now we create the filtered positions Dataframe that contains the rows with the specific vessel_id selected.

In [13]:
# Define the selected vessel ID and date
sel_vessel_id = '5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b16077c9c38969fb2de'
sel_date = datetime.strptime('2019-08-16', '%Y-%m-%d')

# Creating the filtered positions Dataframe that contains the rows with the specific vessel_id selected
filtered_positions = gdf_positions[(gdf_positions['vessel_id'] == sel_vessel_id) & (gdf_positions['t'].dt.date == sel_date.date())]

# Get the number of data points recorded for the selected vessel on the selected date
num_points = len(filtered_positions)

print(f"The number of data points recorded for the vessel with ID {sel_vessel_id} on {sel_date.date()} is: {num_points}")

The number of data points recorded for the vessel with ID 5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b16077c9c38969fb2de on 2019-08-16 is: 18548


In [14]:
filtered_positions.head(10)

id                                          vessel_id  \
825454   6027068  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5768659  2825544  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510789  2455473  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510798  2455484  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510807  2455499  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510813  2455510  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510826  2455525  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510837  2455542  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510850  2455558  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   
5510859  2455570  5de00399a2fdba5f2eb761a622a79a73af9d4058d51e6b...   

                          t       lon      lat heading course speed  \
825454  2019-08-16 00:00:00  23.64103  37.9449                    0   
5768659 2019-08-16 00:00:00  23.64103  37.9449                    0   
5510789 2019-08-16 00:00:08  23.64103  37.9449                    0   
5510798 2019-08-16 00:00:12  23.64103  37.9449                    0   
5510807 2019-08-16 00:00:16  23.64104  37.9449                    0   
5510813 2019-08-16 00:00:20  23.64104  37.9449                    0   
5510826 2019-08-16 00:00:24  23.64104  37.9449                    0   
5510837 2019-08-16 00:00:28  23.64104  37.9449                    0   
5510850 2019-08-16 00:00:32  23.64104  37.9449                    0   
5510859 2019-08-16 00:00:36  23.64104  37.9449                    0   

                                         location_geometry distance_in_meters  \
825454   0101000020E610000040C1C58A1AA43740C5FEB27BF2F8...  559.9576299619398   
5768659  0101000020E610000040C1C58A1AA43740C5FEB27BF2F8...  559.9576299619398   
5510789  0101000020E610000040C1C58A1AA43740C5FEB27BF2F8...  559.9576299619398   
5510798  0101000020E610000040C1C58A1AA43740C5FEB27BF2F8...  559.9576299619398   
5510807  0101000020E6100000876D8B321BA43740C5FEB27BF2F8...  559.0974722598087   
5510813  0101000020E6100000876D8B321BA43740C5FEB27BF2F8...  559.0974722598087   
5510826  0101000020E6100000876D8B321BA43740C5FEB27BF2F8...  559.0974722598087   
5510837  0101000020E6100000876D8B321BA43740C5FEB27BF2F8...  559.0974722598087   
5510850  0101000020E6100000876D8B321BA43740C5FEB27BF2F8...  559.0974722598087   
5510859  0101000020E6100000876D8B321BA43740C5FEB27BF2F8...  559.0974722598087   

        geometry  
825454      None  
5768659     None  
5510789     None  
5510798     None  
5510807     None  
5510813     None  
5510826     None  
5510837     None  
5510850     None  
5510859     None

The new filtered positions Dataframe contains 18548 rows of different Timestamps for the selected ID. To find the minimum, average and maximum time difference we have to sort first the data based on Timestamp.

In [15]:
# Sorting Dataframe based on Timestamp and finding the Time difference between them 
filtered_positions['t'] = pd.to_datetime(filtered_positions['t']) # Convert the 't' column to datetime format for timestamp manipulation
filtered_positions.sort_values(by='t', inplace=True) # Sort the DataFrame based on the 't' (timestamp) column in ascending order
filtered_positions['time_diff'] = filtered_positions['t'].diff().dt.total_seconds() # Calculate the time difference between consecutive timestamps and store it in 'time_diff' column

# Find the minimum, average, and maximum time differences
min_time_diff = filtered_positions['time_diff'].min()
avg_time_diff = filtered_positions['time_diff'].mean()
max_time_diff = filtered_positions['time_diff'].max()

print(f"Minimum Time Difference: {min_time_diff} seconds")
print(f"Average Time Difference: {avg_time_diff} seconds")
print(f"Maximum Time Difference: {max_time_diff} seconds")

Minimum Time Difference: 0.0 seconds
Average Time Difference: 4.658219658165741 seconds
Maximum Time Difference: 6792.0 seconds


**The results from the time analysis provide insights into the time intervals between recorded positions for the selected passenger vessel on August 16, 2019. The minimum time difference of 0 indicates that there are duplicate rows in the dataset. On average, the vessel's position was recorded roughly every 4.66 seconds. The maximum time difference was 6792 seconds, which is equivalent to approximately 1 hours and 53 minutes.This indicates that there were instances where there was a significant gap between position recordings, potentially suggesting periods when the vessel was not actively tracked.**

****

### **Task 2:** Based on the consecutive points, what was the maximum speed reached by the specific vessel on that day? Taking into account the geographical points we have for the ports, which of the northwestern ports was it close to (distance < 0.5 nautical miles)?

In [16]:
# Create Points from lon and lat in the geometry data with global crs ('EPSG:4326)
gdf_ports = gpd.GeoDataFrame(gdf_ports, geometry=gpd.points_from_xy(gdf_ports.lon, gdf_ports.lat), crs='EPSG:4326')
gdf_positions = gpd.GeoDataFrame(gdf_positions, geometry=gpd.points_from_xy(gdf_positions.lon, gdf_positions.lat), crs='EPSG:4326')
filtered_positions = gpd.GeoDataFrame(filtered_positions, geometry=gpd.points_from_xy(filtered_positions.lon, filtered_positions.lat), crs='EPSG:4326')

In [17]:
gdf_positions.t.is_monotonic_increasing

True

In [18]:
gdf_ports.geometry.head()

0    POINT (23.64899 37.93486)
1    POINT (23.05575 37.91680)
2    POINT (24.06864 37.74283)
3    POINT (24.01164 38.02345)
4    POINT (23.56732 37.96085)
Name: geometry, dtype: geometry

In [19]:
filtered_positions.geometry.head()

825454     POINT (23.64103 37.94490)
5768659    POINT (23.64103 37.94490)
5510789    POINT (23.64103 37.94490)
5510798    POINT (23.64103 37.94490)
5510807    POINT (23.64104 37.94490)
Name: geometry, dtype: geometry

In this task we have to find first the maximum velocity that the boat of the previous task had and next in which ports were found near 0.5nm. We know that 1 nm is 1852 m, so 0.5 nm is equal 926 m.

In [20]:
# Assuming our data in global crs (EPSG:4326)
filtered_positions.crs = "EPSG:4326"
gdf_ports.crs = "EPSG:4326"

# Now, you can transform them to EPSG:2100
filtered_positions = filtered_positions.to_crs("EPSG:2100")
gdf_ports = gdf_ports.to_crs("EPSG:2100")

In [21]:
gdf_ports.geometry.head()

0    POINT (469005.261 4198357.777)
1    POINT (416852.900 4196716.187)
2    POINT (505897.863 4176996.265)
3    POINT (500872.081 4208129.017)
4    POINT (461841.829 4201271.603)
Name: geometry, dtype: geometry

In [22]:
filtered_positions.geometry.head()

825454     POINT (468310.060 4199474.399)
5768659    POINT (468310.060 4199474.399)
5510789    POINT (468310.060 4199474.399)
5510798    POINT (468310.060 4199474.399)
5510807    POINT (468310.939 4199474.396)
Name: geometry, dtype: geometry

As we can see the geometry column has already changed and we can calculate the difference between consecutive points which is Δs. We have already calculated the Δt as time diff in the previous task, so we can now calculate the velocity of each point based on the formula   𝑣 = 𝛥𝑠/𝛥𝑡.

#

## **The Reason Why We Use The Mathematical Formula u = Δs / Δt**

### **Distance Calculation**

### Note #1 (Regarding Distance Between Two Geographic Points)

- When working with geographic coordinates in latitude (x) and longitude (y), it's important to consider that these coordinates are polar and measured in degrees. This means that the direct application of the Pythagorean theorem, which gives us the distance between two points with Cartesian coordinates (x, y) (i.e., on a flat plane), measured in meters, is not valid.

- To calculate the distance between two points with geographic coordinates, we need to convert the difference in latitude and longitude (in degrees) into meters. Let's say we have approximate conversions, x and y (for latitude and longitude, respectively), and then apply the Pythagorean theorem: 𝑑 = √(𝑥^2 + 𝑦^2). 

- The conversion factor between degrees and meters for a given region can be determined, for example, by measuring the distance between two known coordinates using tools like Google Maps.

### **Velocity Calculation**

### Note #2 (Regarding Ship Velocity)

- While there is a 'speed' field in the database (DB), it may not always be considered reliable for our analyses. Sometimes, we prefer to calculate the instantaneous velocity of a vessel at a specific time (t) based on the displacement from the previous recorded time. 

- The formula for calculating velocity (v) is: 𝑣 = 𝛥𝑠 / 𝛥𝑡, where Δs represents the distance traveled, and Δt is the time interval. To calculate Δs for geographic coordinates (lat/lon), refer to Note #1.

### Closing Remark

These notes provide essential information on distance calculations between geographic points and the calculation of vessel velocities in geospatial analysis.

In [23]:
distances = [] # Initialize a list to store calculated distances

# Calculate distances between consecutive points in the 'filtered_positions' DataFrame
for i in range(len(filtered_positions) - 1):
    distance = filtered_positions.geometry.iloc[i].distance(filtered_positions.geometry.iloc[i + 1])
    distances.append(distance)

# Set None in the first place because you can't calculate the first row of distance and name the distance column between points Δs
filtered_positions['Δs'] = [None] + distances

# Calculate velocity based on the mathematical formula u = Δs / Δt
filtered_positions['velocity'] = filtered_positions['Δs'] / filtered_positions['time_diff']

# Find the row with the maximum velocity of the ship
max_velocity_row = filtered_positions[filtered_positions['velocity'] == filtered_positions['velocity'].max()]

print("Row with Maximum Velocity:")
print(max_velocity_row[['id', 't', 'Δs', 'time_diff', 'velocity', 'speed']])

Row with Maximum Velocity:
             id                   t         Δs  time_diff   velocity speed
750116  5916984 2019-08-16 15:52:36  45.980518        4.0  11.495129  15.4


Now that we have already found the Timestamp with the maximum velocity let's find the ports that the boat found near.

In [24]:
# Initialize an empty list to store port names within a certain distance from vessels
list = []

for row, column in filtered_positions.iterrows():
    vessel_geom = column['geometry']
    
    for row, column in gdf_ports.iterrows():
        port_geom = column['geometry']

        # Calculate the distance between the vessel and the port
        distance_to_vessel = vessel_geom.distance(port_geom)
    
        # Check if the distance is within 0.5 nautical miles (1 n.m. = 1852 meters)
        if distance_to_vessel <=  0.5 * 1852:
            list.append(column['name'])

# Create a list of unique nearby port names
nearby_ports = []
for item in list:
   if item not in nearby_ports:
       nearby_ports.append(item)

print("Ports in distance under 0.5 miles:\n")    
for item in nearby_ports:
   print(item)

Ports in distance under 0.5 miles:

PIREAUS - KENTRIKOS LIMENAS
PIRAEUS - AKTI VASILIADI


Visualize the positions of vessels and ports.

In [25]:
from mpl_toolkits.axes_grid1 import make_axes_locatable

# Convert the 't' column to a string format for better visualization labels
filtered_positions['t_str'] = filtered_positions['t'].dt.strftime('%Y-%m-%d %H:%M:%S')

# Create a basemap using 'gdf_ports' with ports marked in red
m = gdf_ports.explore(color='red')

# Create a visualization of vessel positions overlaid on the basemap
filtered_positions[['vessel_id', 't_str', 'geometry']].explore(m = m, column='vessel_id')

**The results show that the vessel was near 2 ports PIRAEUS - AKTI VASILIADI and PIREAUS - KENTRIKOS LIMENAS. From the visualization, we can see that the vessel performs a trip from Piraeus to Aegina and back, but we don't have the port of Aegine at close ports. That means for some reason there is no point of vessel near the port.**

****

## Step 4: Cleaning Data 

### Task 3: Are there waypoints that belong to the same vessel and occur at the same moment in time or have a time difference of less than 5 seconds? If we identify such pairs of records, we should keep only one record and delete the other.

In this section, we perform data cleaning to handle duplicate timestamps in the data locations and nearby timestamps. First, we convert the 't' column in the positions DataFrame to a datetime format. Next, we sort the positions DataFrame based on the 't' column. At the end we remove the duplicates rows.

In [26]:
gdf_positions['t'] = pd.to_datetime(gdf_positions['t'])
gdf_positions.sort_values(by='t', inplace=True)
print('Before Drop Duplicates we have ', len(gdf_positions), 'points')

# Group the DataFrame by 'vessel_id' and drop duplicate rows based on the 't' column, keeping the first occurrence
gdf_positions = gdf_positions.groupby('vessel_id').apply(lambda group: group.drop_duplicates(subset='t', keep='first'))
gdf_positions.reset_index(drop=True, inplace=True)
print('After Drop Duplicates we have ', len(gdf_positions), 'points')

Before Drop Duplicates we have  7036651 points
After Drop Duplicates we have  4852667 points


By removing duplicates from 7 million rows they were reduced to about 4.8 million.

Next we identifie and remove rows with timestamps that are very close (less than 5 seconds) to each other within the same 'vessel_id'.

In [27]:
# Initialize a list to store the indices of rows to remove
rows_to_remove = []

for vessel_id, group_df in gdf_positions.groupby('vessel_id'):
    # Calculate time differences between consecutive timestamps
    time_diff = group_df['t'].diff().dt.total_seconds()
    # Select rows with time differences less than 5 seconds (potentially duplicate entries)
    close_timestamps = group_df[time_diff < 5]
    
    # If there are rows with close timestamps (diff < 5), add their indices to the list of rows to remove
    if not close_timestamps.empty:
        rows_to_remove.extend(close_timestamps.index)

# Drop the identified rows with close timestamps from the DataFrame and reset the index to have a clean and continuous DF
gdf_positions1 = gdf_positions.drop(rows_to_remove)
gdf_positions1.reset_index(drop=True, inplace=True)

print('After this procedure the remaining data are about', len(gdf_positions1))

### Task 4: Are there waypoints (in the Positions table) that indicate a speed greater than the maximum allowable speed for the specific type of vessel? If yes, we should remove the records that indicate a speed greater than the maximum allowable speed for that particular vessel type.

In this Step we first add the required columns in vessels_df and vesselstypes_df adding approximately available speed_max that we get for the different types of vessels that we have in the data. This created the required database schema.

First, we keep the data in a new DataFrame and then transform the coordinate system of the positions data to EPSG:2100 to ensure consistency in spatial calculations.

In [ ]:
new_positions = gdf_positions1.to_crs("EPSG:2100")

We want to remove rows that have a velocity greater than max available speed. For this reason we calculate the velocity as in the previous queries for each vessel id.

In [ ]:
# Define a function to calculate Δs (distance between consecutive points) for a DataFrame
def calculate_delta_s(df):
    distances = []
    for i in range(len(df) - 1):
        distance = df.geometry.iloc[i].distance(df.geometry.iloc[i + 1])
        distances.append(distance)
    df['Δs'] = [None] + distances
    return df

# Define a function to calculate Δt (time difference) and velocity for a DataFrame
def calculate_delta_t_and_velocity(df):
    if df.t.is_monotonic_increasing == True:
        df['Δt'] = df['t'].diff().dt.total_seconds()
    else:
        print('The time of points is not monotonic increase')
    
    # Calculate velocity using the formula: velocity = Δs / Δt
    df['velocity'] = df['Δs'] / df['Δt']
    return df

In [ ]:
# Initialize a list to store group DataFrames
group_dfs = []

# Group 'new_positions' DataFrame by 'vessel_id' and apply calculations to each group
for vessel_id, group_df in new_positions.groupby('vessel_id'):
    # Calculate Δs for the group and append it to the list
    group_df = calculate_delta_s(group_df)
    group_dfs.append(group_df)

    # Calculate Δt and velocity for the group
    group_df = calculate_delta_t_and_velocity(group_df)

# Clear 'new_positions' DataFrame to prepare for concatenation
new_positions = new_positions.iloc[0:0]

# Concatenate the calculated group DataFrames into a new GeoDataFrame
new_positions = gpd.GeoDataFrame(pd.concat(group_dfs, ignore_index=True), geometry='geometry')

We transform the velocity column in knots to compare them with the max available speed.

In [ ]:
def meters_per_seconds_to_knots(speed):
    knots = speed * 1.94384449
    return knots
    
new_positions['velocity in knots'] = new_positions['velocity'].apply(meters_per_seconds_to_knots)

We update the 'vessels_df' DataFrame to include information about vessel types and their maximum speeds. 

In [ ]:
vessels_df['type'] = vessels_df['type'].fillna(-1).astype(int)
vessels_df['speed_max'] = 0
vessels_df.loc[vessels_df['type'] == 25, 'speed_max'] = 216
vessels_df.loc[vessels_df['type'] == 30, 'speed_max'] = 20
vessels_df.loc[vessels_df['type'] == 31, 'speed_max'] = 12
vessels_df.loc[vessels_df['type'] == 36, 'speed_max'] = 20
vessels_df.loc[vessels_df['type'] == 37, 'speed_max'] = 30
vessels_df.loc[vessels_df['type'].between(40, 49), 'speed_max'] = 50
vessels_df.loc[vessels_df['type'] == 50 , 'speed_max'] = 25
vessels_df.loc[vessels_df['type'] == 51 , 'speed_max'] = 40
vessels_df.loc[vessels_df['type'] == 52 , 'speed_max'] = 12
vessels_df.loc[vessels_df['type'] == 54 , 'speed_max'] = 8
vessels_df.loc[vessels_df['type'].between(60, 69), 'speed_max'] = 25
vessels_df.loc[vessels_df['type'].between(70, 79), 'speed_max'] = 20
vessels_df.loc[vessels_df['type'].between(80, 89), 'speed_max'] = 20

Next we merge 'new_positions' with 'vessels_df' to access information about vessel types and maximum speeds.

In [ ]:
pos = new_positions.merge(vessels_df[['id',"type",'speed_max']], left_on='vessel_id', right_on='id', how='left')
pos.drop(columns=['id_y'], inplace=True)

# Filter rows based on velocity, type, and speed_max criteria
pos = pos[(pos['velocity in knots'] <= pos['speed_max']) | (pos['type'] == -1) | pos['velocity in knots'].isna()]

# Exclude rows where 'speed_max' is zero
pos = pos[pos['speed_max'] != 0]

pos.reset_index(drop=True, inplace=True)

In [36]:
pos.head(10)

id_x                                          vessel_id  \
0   56775  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
1  104599  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
2  197026  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
3  226340  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
4  249045  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
5  252333  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
6  257233  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
7  263839  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
8  282698  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
9  293132  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   

                     t       lon       lat  heading  course  speed  \
0  2019-08-01 02:52:35  23.53248  38.02678     11.0   256.9    0.0   
1  2019-08-01 06:10:36  23.53245  38.02678     10.0   302.7    0.0   
2  2019-08-01 10:28:35  23.53255  38.02612    335.0   266.9    0.0   
3  2019-08-01 12:10:37  23.53175  38.02600     28.0   243.4    0.0   
4  2019-08-01 13:28:36  23.53196  38.02584     22.0   191.8    0.2   
5  2019-08-01 13:40:36  23.53216  38.02584      4.0   214.0    0.0   
6  2019-08-01 13:58:37  23.53271  38.02582      6.0    89.5    0.5   
7  2019-08-01 14:22:36  23.53189  38.02576     24.0   155.1    0.3   
8  2019-08-01 15:40:36  23.53214  38.02578     24.0    89.6    0.1   
9  2019-08-01 16:28:36  23.53214  38.02575      9.0   231.5    0.0   

                                   location_geometry  distance_in_meters  \
0  0101000020E61000002AC6F99B50883740EC17EC866D03...        13646.902437   
1  0101000020E610000055C1A8A44E883740EC17EC866D03...        13648.848561   
2  0101000020E61000001C7C613255883740C1E270E65703...        13593.123862   
3  0101000020E6100000E3A59BC42088374017D9CEF75303...        13636.377957   
4  0101000020E6100000B9C7D2872E883740DE76A1B94E03...        13610.803373   
5  0101000020E6100000473D44A33B883740DE76A1B94E03...        13597.741546   
6  0101000020E61000008E40BCAE5F88374097CADB114E03...        13560.386888   
7  0101000020E6100000C7116BF129883740C1C58A1A4C03...        13609.453840   
8  0101000020E6100000B8E4B8533A883740087250C24C03...        13594.598947   
9  0101000020E6100000B8E4B8533A8837409EEFA7C64B03...        13592.375461   

                                           geom         Δs       Δt  velocity  \
0  POINT (458818.04814661463 4208601.550547703)        NaN      NaN       NaN   
1   POINT (458815.4151503135 4208601.563782826)   2.633030  11881.0  0.000222   
2    POINT (458823.8237752401 4208528.29000446)  73.754672  15479.0  0.004765   
3   POINT (458753.5428815002 4208515.328692883)  71.466073   6122.0  0.011674   
4   POINT (458771.8847206099 4208497.483282045)  25.590657   4679.0  0.005469   
5   POINT (458789.4382538119 4208497.394972182)  17.553755    720.0  0.024380   
6  POINT (458837.69932105555 4208494.933234184)  48.323812   1081.0  0.044703   
7   POINT (458765.6963120004 4208488.637877213)  72.277692   1439.0  0.050228   
8   POINT (458787.6494144137 4208490.746559865)  22.054144   4680.0  0.004712   
9   POINT (458787.6326713889 4208487.417939089)   3.328663   2880.0  0.001156   

   speed_m/s  velocity in knots  type  speed_max  
0     0.0000                NaN    89         20  
1     0.0000           0.000431    89         20  
2     0.0000           0.009262    89         20  
3     0.0000           0.022692    89         20  
4     0.1028           0.010631    89         20  
5     0.0000           0.047391    89         20  
6     0.2570           0.086895    89         20  
7     0.1542           0.097635    89         20  
8     0.0514           0.009160    89         20  
9     0.0000           0.002247    89         20

**In this section, we apply filters to the positions data based on vessel type, maximum speed, and allowable speed. This filtering ensures that only valid positions are retained for further analysis. While examining the 'vessels' and 'vesselstypes' tables, we encountered cases where vessels lacked information about their type or maximum speed. This absence of information could be due to data gaps or a lack of specific indicators for vessel types. To address this, we made the decision to exclude positions associated with these vessels from our analysis. By applying these filters, we prioritize data quality and relevance, focusing on positions that can provide meaningful insights for subsequent analyses.**

In [35]:
len(pos)

3607379

After the cleaning procedure, we have successfully refined it, leaving us with approximately 3.6 million data entries. Dataset's quality has significantly improved, making it more suitable for subsequent maritime data analysis and insights.

In [ ]:
#pos.to_csv('../Dataset_after/clean.csv')